# TunisAir Delay Prediction

In [1]:
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd


import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go

from sklearn.linear_model import Lasso, LogisticRegression, LinearRegression, RidgeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, RandomForestRegressor, GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor
from sklearn.neural_network import MLPRegressor, MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn import metrics

from statsmodels import api as sm

# Data Exploration

In [2]:
train = pd.read_csv('Train.csv', sep=',', infer_datetime_format=True)
test = pd.read_csv('Test.csv', sep=',', infer_datetime_format=True)

In [3]:
train.sample(5)

ID       DATOP     FLTID DEPSTN ARRSTN  \
85682    train_id_85682  2018-04-27  TU 9011     SFA    DJE   
4156      train_id_4156  2016-02-15  TU 0527     DUS    TUN   
18450    train_id_18450  2016-02-25  TU 6042     JED    TUN   
103998  train_id_103998  2018-12-04  TU 0791     LHR    TUN   
100423  train_id_100423  2018-10-17  TU 0527     DUS    TUN   

                        STD                  STA STATUS         AC  target  
85682   2018-04-27 12:40:00  2018-04-27 13.15.00    ATA  TU 736IOK     0.0  
4156    2016-02-15 11:55:00  2016-02-15 14.35.00    ATA  TU 736IOR    12.0  
18450   2016-02-25 01:50:00  2016-02-25 06.50.00    ATA  TU 320IMW     7.0  
103998  2018-12-04 16:50:00  2018-12-04 19.50.00    ATA  TU 32AIMD    29.0  
100423  2018-10-17 14:00:00  2018-10-17 16.40.00    ATA  TU 32AIMP    33.0

In [23]:
test.tail()

ID       DATOP      FLTID DEPSTN ARRSTN                  STD  \
9328  test_id_9328  2018-09-12   TU 0998     TUN    NCE  2018-09-12 14:15:00   
9329  test_id_9329  2018-09-27  WKL 0000     TUN    TUN  2018-09-27 22:00:00   
9330  test_id_9330  2018-09-03   UG 1601     SJJ    TUN  2018-09-03 09:20:00   
9331  test_id_9331  2018-09-15   UG 0008     TUN    DJE  2018-09-15 14:30:00   
9332  test_id_9332  2018-09-19   UG 0009     DJE    TUN  2018-09-19 16:15:00   

                      STA STATUS         AC  
9328  2018-09-12 15.45.00    ATA  TU 320IMV  
9329  2018-09-28 01.00.00    SCH  TU 32AIMG  
9330  2018-09-03 11.10.00    SCH  TU CR9ISA  
9331  2018-09-15 15.30.00    SCH  UG AT7LBD  
9332  2018-09-19 17.15.00    SCH  UG AT7LBD

In [4]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 107833 entries, 0 to 107832
Data columns (total 10 columns):
ID        107833 non-null object
DATOP     107833 non-null object
FLTID     107833 non-null object
DEPSTN    107833 non-null object
ARRSTN    107833 non-null object
STD       107833 non-null object
STA       107833 non-null object
STATUS    107833 non-null object
AC        107833 non-null object
target    107833 non-null float64
dtypes: float64(1), object(9)
memory usage: 8.2+ MB


In [5]:
train.describe()

target
count  107833.000000
mean       48.733013
std       117.135562
min         0.000000
25%         0.000000
50%        14.000000
75%        43.000000
max      3451.000000

In [6]:
train.isnull().sum()

ID        0
DATOP     0
FLTID     0
DEPSTN    0
ARRSTN    0
STD       0
STA       0
STATUS    0
AC        0
target    0
dtype: int64

In [8]:
train['DEPSTN'].nunique()

132

In [12]:
train['STATUS'].unique()

array(['ATA', 'DEP', 'RTR', 'SCH', 'DEL'], dtype=object)

In [25]:
train['AC'].nunique()

68

# Data Visualisation

In [21]:
px.line(train, x='DATOP', y='target')

In [14]:
px.histogram(train,x='STATUS')

In [22]:
px.histogram(test,x='STATUS')

## Feature Extraction

In [28]:
print(train.columns)
print(test.columns)

Index(['ID', 'DATOP', 'FLTID', 'DEPSTN', 'ARRSTN', 'STD', 'STA', 'STATUS',
       'AC', 'target'],
      dtype='object')
Index(['ID', 'DATOP', 'FLTID', 'DEPSTN', 'ARRSTN', 'STD', 'STA', 'STATUS',
       'AC'],
      dtype='object')


In [ ]:
train.drop(columns=['DATOP', 'FLTID','STD', 'STA','AC'], inplace=True)
test.drop(columns=['DATOP', 'FLTID','STD', 'STA','AC'], inplace=True)

In [ ]:
## RMSE is the evaluation metric and use of regression to predict